# Schuhgröße synthetisch WS 2025 (Notebook)

Erstellt von ChatGPT (Modell 4o oder 5?), 2025-10-25

Promt etwas so:

> Erzeuge einen synthetischen Datensatz mit Alter, Geschlecht, Körpergröße, Schuhgröße 

ChatGPT: 

Gut, ich kann dir einen synthetischen Datensatz erzeugen, der näher an den echten Wachstums-Standards der World Health Organization (WHO) liegt. Dabei liegt der Fokus auf Alter, Geschlecht, Körpergröße — Schuhgröße kann ich zusätzlich approximieren (wenngleich Wertsätze dafür weniger standardisiert verfügbar sind).

Vorgehensweise:
*  Ich verwende die WHO-Wachstumsstandards für „Länge/Höhe-für-Alter“ (Height-for-age) als Referenz. 
* ...
* Jeder Wert (Körpergröße) wird so generiert, dass er sich innerhalb realistischer Perzentilen-Spannen für das betreffende Alter und Geschlecht befindet.
* Schuhgröße wird anhand der Körpergröße geschätzt – z. B. grobe Zuordnung: je 5 cm Körpergröße mehr → ca. eine EU-Schuhgröße mehr.


> Füge noch den BMI hinzu

Da der Datensatz Personen von 3 bis 40 Jahren enthält, unterscheiden wir zwei Fälle:

Kinder & Jugendliche (< 18 Jahre), vereinfacht orientiert an WHO-Perzentilen (ungefähre Richtwerte):

* < 5. Perzentile (≈ BMI < 14–15): Untergewichtig
* 5.–85. Perzentile (≈ BMI 14–22): Normalgewicht
* 85.–95. Perzentile (≈ BMI 22–25): Übergewichtig
* ≥ Perzentile (≈ BMI > 25): Adipositas

Erwachsene (≥ 18 Jahre), nach WHO-Klassifikation:

* < 18.5 → Untergewichtig
* 18.5–24.9 → Normalgewicht
* 25–29.9 → Übergewichtig
* ≥ 30 → Adipositas

(Die Werte für Kinder sind hier bewusst grob gehalten, da exakte Perzentilen tabellenabhängig sind.)

In [1]:
import csv
import random

## 1. Wachstum & BMI Referenz für Kinder & Jugendliche ---

In [2]:
growth_reference = {
    3: {"m": 96, "w": 95},
    5: {"m": 110, "w": 109},
    10: {"m": 140, "w": 139},
    12: {"m": 152, "w": 151},
    13: {"m": 158, "w": 156},
    14: {"m": 165, "w": 160},
    15: {"m": 170, "w": 163},
    16: {"m": 174, "w": 165},
    17: {"m": 177, "w": 166},
    18: {"m": 178, "w": 167},
    19: {"m": 179, "w": 167},
    20: {"m": 179, "w": 167},
    21: {"m": 179, "w": 167}
}

bmi_reference = {
    3: 15, 5: 15.5, 10: 17, 12: 18, 13: 19,
    14: 20, 15: 21, 16: 21.5, 17: 22, 18: 22.5,
    19: 23, 20: 23.5, 21: 24
}

In [3]:
def interpolate_height(age, gender):
    if age in growth_reference:
        return growth_reference[age][gender]
    lower_ages = [a for a in growth_reference if a < age]
    upper_ages = [a for a in growth_reference if a > age]
    low = max(lower_ages)
    high = min(upper_ages)
    low_val = growth_reference[low][gender]
    high_val = growth_reference[high][gender]
    return low_val + (high_val - low_val) * (age - low) / (high - low)

In [4]:
def interpolate_bmi(age):
    if age in bmi_reference:
        return bmi_reference[age]
    lower_ages = [a for a in bmi_reference if a < age]
    upper_ages = [a for a in bmi_reference if a > age]
    low = max(lower_ages)
    high = min(upper_ages)
    low_val = bmi_reference[low]
    high_val = bmi_reference[high]
    return low_val + (high_val - low_val) * (age - low) / (high - low)

In [5]:
def estimate_shoe_size(height_cm):
    foot_length = height_cm * 0.15
    return round((foot_length + 1.5) * 1.5)

## BMI-Kategorie bestimmen

In [6]:
def bmi_category(age, bmi):
    if age < 18:  # grobe Einteilung für Kinder & Jugendliche
        if bmi < 15:
            return "Untergewichtig"
        elif bmi < 22:
            return "Normalgewicht"
        elif bmi < 25:
            return "Übergewichtig"
        else:
            return "Adipositas"
    else:  # Erwachsene
        if bmi < 18.5:
            return "Untergewichtig"
        elif bmi < 25:
            return "Normalgewicht"
        elif bmi < 30:
            return "Übergewichtig"
        else:
            return "Adipositas"

## Kinder & Jugendliche (3-21 Jahre)

In [7]:
rows = []
for i in range(1, 1001):
    age = random.randint(3, 21)
    gender = random.choice(["m", "w"])
    base_height = interpolate_height(age, gender)
    height = round(random.gauss(base_height, 5), 1)
    base_bmi = interpolate_bmi(age)
    bmi = round(random.gauss(base_bmi, 2), 1)
    weight = round(bmi * (height / 100) ** 2, 1)
    shoe_size = estimate_shoe_size(height)
    cat = bmi_category(age, bmi)
    rows.append([i, age, gender, height, weight, bmi, cat, shoe_size])

## Erwachsene (22-40 Jahre)

In [8]:
adult_mean_height = {"m": 179, "w": 167}
adult_height_sd = 6
adult_bmi_mean = {"m": 25, "w": 24}
adult_bmi_sd = 3

for i in range(1001, 1501):
    age = random.randint(22, 40)
    gender = random.choice(["m", "w"])
    height = round(random.gauss(adult_mean_height[gender], adult_height_sd), 1)
    bmi = round(random.gauss(adult_bmi_mean[gender], adult_bmi_sd), 1)
    weight = round(bmi * (height / 100) ** 2, 1)
    shoe_size = estimate_shoe_size(height)
    cat = bmi_category(age, bmi)
    rows.append([i, age, gender, height, weight, bmi, cat, shoe_size])

## CSV speichern

In [9]:
filename = "synthetische_daten_3bis40_mit_BMI_Kategorien.csv"
with open(filename, "w", newline="", encoding="utf-8") as f:
    writer = csv.writer(f)
    writer.writerow([
        "ID", "Alter_Jahre", "Geschlecht", "Körpergröße_cm", "Gewicht_kg", "BMI", "BMI_Kategorie", "Schuhgröße_EU"
    ])
    writer.writerows(rows)

print(f"Datei '{filename}' mit {len(rows)} Einträgen und BMI-Kategorien erfolgreich erstellt.")

Datei 'synthetische_daten_3bis40_mit_BMI_Kategorien.csv' mit 1500 Einträgen und BMI-Kategorien erfolgreich erstellt.
